# 1. import modules

In [1]:
## Code based on WGAN implementation in https://github.com/eriklindernoren/Keras-GAN

import numpy as np
import tensorflow
from sklearn.base import BaseEstimator, TransformerMixin
from keras.layers.merge import _Merge
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import RMSprop
from functools import partial
import keras.backend as K

%matplotlib inline
import numpy as np
import mdtraj as md
import nglview as nv
import dmaps
from scipy.spatial.distance import pdist, squareform
import matplotlib.pyplot as plt
from numpy import matlib as mb
from mpl_toolkits.mplot3d import Axes3D
import pandas as pd

from keras.utils import get_custom_objects, plot_model
from nglview.contrib.movie import MovieMaker
import moviepy.editor as mpy

/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:529: FutureWarning: Passing (type, 1) or 

_ColormakerRegistry()

# 2. Load aligned real trajectories 

In [2]:
real_data = np.loadtxt('traj_align_161.txt')

In [3]:
real_data.shape

(50001, 72)

# 3. Load Latent Space

In [4]:
latent_space = np.loadtxt('all-atom latent space.txt')[:,:2]

In [5]:
latent_space.shape

(50001, 2)

# 4. Training GAN Model

In [19]:
__all__ = ['MolGen']

In [20]:
def swish(x):
    return (K.sigmoid(x) * x)

In [21]:
class RandomWeightedAverage(_Merge):
    
    def __init__(self, batch_size):
        _Merge.__init__(self)
        self.batch_size=batch_size


    """Provides a (random) weighted average between real and generated image samples"""
    def _merge_function(self, inputs):
        alpha = K.random_uniform((self.batch_size, 1))
        return (alpha * inputs[0]) + ((1 - alpha) * inputs[1])

In [24]:
class MolGen(BaseEstimator, TransformerMixin):

    def __init__(self, latent_dim, output_dim, batch_size=20000, noise_variance=0.1,
                n_epochs=100000,
                hidden_layer_depth=3, hidden_size=200, activation='swish', verbose=True,
                n_discriminator=5):
        self.latent_dim = latent_dim
        self.output_dim = output_dim
        self.hidden_layer_depth = hidden_layer_depth
        self.hidden_size = hidden_size
        self.activation = activation
        self.batch_size=batch_size
        self.n_epochs = n_epochs
        self.noise_variance = noise_variance
        self.verbose = verbose

        self.n_discriminator = n_discriminator
        optimizer = RMSprop(lr=0.00005)

        # Register swish
        get_custom_objects().update({'swish': swish})

        # Build generator and discriminator 
        self.generator = self._build_generator()
        self.discriminator = self._build_discriminator()

        #
        # Construct computational graph for discriminator
        #
        self.generator.trainable = False 

        # Real molecule 
        real_mol = Input(shape=(self.output_dim,))

        # Discriminator input 
        z_disc = Input(shape=(self.latent_dim,))
        fake_mol = self.generator(z_disc)

        # Discriminator does its job 
        fake = self.discriminator(fake_mol)
        valid = self.discriminator(real_mol)

        # Interpolated between real and fake molecule.
        interp_mol = RandomWeightedAverage(batch_size=self.batch_size)([real_mol, fake_mol])
        validity_interp = self.discriminator(interp_mol)

        # Use Python partial to provide loss function with additional
        # 'averaged_samples' argument
        partial_gp_loss = partial(self.ـgradient_penalty_loss,
                          averaged_samples=interp_mol)
        partial_gp_loss.__name__ = 'gradient_penalty' # Keras requires function names

        self.discriminator_model = Model(inputs=[real_mol, z_disc],
                            outputs=[valid, fake, validity_interp])
        self.discriminator_model.compile(loss=[self._wasserstein_loss,
                                        self._wasserstein_loss,
                                        partial_gp_loss],
                                        optimizer=optimizer,
                                        loss_weights=[1, 1, 10])

        # 
        # Construct computational graph for generator 
        # 
        self.discriminator.trainable = False
        self.generator.trainable = True

        z_gen = Input(shape=(self.latent_dim,))
        mol = self.generator(z_gen)
        valid = self.discriminator(mol)
        self.generator_model = Model(z_gen, valid)
        self.generator_model.compile(loss=self._wasserstein_loss, optimizer=optimizer)

        self.is_fitted = False


    def fit(self, X, y): 
        # Adversarial ground truths
        valid = -np.ones((self.batch_size, 1))
        fake =  np.ones((self.batch_size, 1))
        dummy = np.zeros((self.batch_size, 1)) # Dummy gt for gradient penalty
        for epoch in range(self.n_epochs):
            for _ in range(self.n_discriminator):
                # ---------------------
                #  Train Discriminator
                # ---------------------

                # Select a random batch of images
                idx = np.random.randint(0, y.shape[0], self.batch_size)
                real_mols = y[idx]

                # Sample generator input
                fake_mols = X[idx]
                fake_mols += np.random.normal(0, self.noise_variance, fake_mols.shape)
                
                # Train the critic
                d_loss = self.discriminator_model.train_on_batch([real_mols, fake_mols],
                                                            [valid, fake, dummy])

            # ---------------------def __init__(self, latent_dim, 
            #  Train Generator
            # ---------------------

            g_loss = self.generator_model.train_on_batch(fake_mols, valid)

            # Plot the progress
            if self.verbose:
                print ("%d [D loss: %f] [G loss: %f]" % (epoch, d_loss[0], g_loss))
        
        self.is_fitted = True
        return self


    def transform(self, X):

        if self.is_fitted:
            out = self.generator.predict(X + np.random.normal(0, self.noise_variance, X.shape), batch_size=self.batch_size)
            return out
        
        raise RuntimeError('Model needs to be fit first.')


    def ـgradient_penalty_loss(self, y_true, y_pred, averaged_samples):
        """
        Computes gradient penalty bas
        #   ... summing over the rows ...ed on prediction and weighted real / fake samples
        """
        gradients = K.gradients(y_pred, averaged_samples)[0]
        # compute the euclidean norm by squaring ...
        gradients_sqr = K.square(gradients)
        #   ... summing over the rows ...
        gradients_sqr_sum = K.sum(gradients_sqr,
                                  axis=np.arange(1, len(gradients_sqr.shape)))
        #   ... and sqrt
        gradient_l2_norm = K.sqrt(gradients_sqr_sum)
        # compute lambda * (1 - ||grad||)^2 still for each single sample
        gradient_penalty = K.square(1 - gradient_l2_norm)
        # return the mean as loss over all the batch samples
        return K.mean(gradient_penalty)


    def _wasserstein_loss(self, y_true, y_pred):
        return K.mean(y_true * y_pred)


    def _build_generator(self):
        model = Sequential()

        model.add(
            Dense(
                self.hidden_size, 
                activation=self.activation, 
                input_dim=self.latent_dim
            )
        )
        for _ in range(self.hidden_layer_depth - 1):
            model.add(Dense(self.hidden_size, activation=self.activation))

        model.add(Dense(self.output_dim, activation='linear'))

        model.summary()

        input = Input(shape=(self.latent_dim,))
        mol = model(input)

        return Model(input, mol)

    def _build_discriminator(self):
        model = Sequential()

        model.add(
            Dense(
                self.hidden_size, 
                activation=self.activation, 
                input_dim=self.output_dim
            )
        )
        for _ in range(self.hidden_layer_depth - 1):
            model.add(Dense(self.hidden_size, activation=self.activation))
        
        model.add(Dense(1))

        model.summary()

        mol = Input(shape=(self.output_dim,))
        validity = model(mol)

        return Model(mol, validity)


In [25]:
#n_components = 2 # Number of eigenfunctions to learn.

model = MolGen(

    latent_dim = 2,
    output_dim = 72,
)


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_9 (Dense)              (None, 200)               600       
_________________________________________________________________
dense_10 (Dense)             (None, 200)               40200     
_________________________________________________________________
dense_11 (Dense)             (None, 200)               40200     
_________________________________________________________________
dense_12 (Dense)             (None, 72)                14472     
Total params: 95,472
Trainable params: 95,472
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_13 (Dense)             (None, 200)               14600     
_________________________________________________________________
dense_

In [26]:
X = np.array(latent_space)
y = np.array(real_data)
slow_modes = model.fit(X,y)

W0821 18:58:13.757910 140190822491968 deprecation.py:323] From /home/beryl/anaconda3/lib/python3.7/site-packages/tensorflow/python/ops/math_grad.py:1250: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
W0821 18:58:13.895379 140190822491968 deprecation_wrapper.py:119] From /home/beryl/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:986: The name tf.assign_add is deprecated. Please use tf.compat.v1.assign_add instead.

W0821 18:58:13.899746 140190822491968 deprecation_wrapper.py:119] From /home/beryl/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:973: The name tf.assign is deprecated. Please use tf.compat.v1.assign instead.



0 [D loss: 4.006197] [G loss: 0.000394]
1 [D loss: 2.377445] [G loss: 0.000258]
2 [D loss: 0.868767] [G loss: 0.000114]
3 [D loss: -0.600660] [G loss: -0.000058]
4 [D loss: -2.063425] [G loss: -0.000305]
5 [D loss: -3.508818] [G loss: -0.000665]
6 [D loss: -4.982584] [G loss: -0.001143]
7 [D loss: -6.393970] [G loss: -0.001739]
8 [D loss: -7.857526] [G loss: -0.002422]
9 [D loss: -9.260253] [G loss: -0.003200]
10 [D loss: -10.669947] [G loss: -0.004081]
11 [D loss: -12.063509] [G loss: -0.005085]
12 [D loss: -13.410523] [G loss: -0.006186]
13 [D loss: -14.747757] [G loss: -0.007417]
14 [D loss: -16.054768] [G loss: -0.008764]
15 [D loss: -17.337603] [G loss: -0.010244]
16 [D loss: -18.590120] [G loss: -0.011818]
17 [D loss: -19.813995] [G loss: -0.013437]
18 [D loss: -20.995657] [G loss: -0.015196]
19 [D loss: -22.165611] [G loss: -0.017041]
20 [D loss: -23.281370] [G loss: -0.018987]
21 [D loss: -24.368790] [G loss: -0.021126]
22 [D loss: -25.395515] [G loss: -0.023469]
23 [D loss: -2

186 [D loss: -37.128304] [G loss: -1.558746]
187 [D loss: -37.108521] [G loss: -1.593410]
188 [D loss: -37.087708] [G loss: -1.608486]
189 [D loss: -37.075325] [G loss: -1.635367]
190 [D loss: -37.056019] [G loss: -1.638107]
191 [D loss: -37.040634] [G loss: -1.669819]
192 [D loss: -37.018650] [G loss: -1.674634]
193 [D loss: -37.000851] [G loss: -1.701653]
194 [D loss: -36.980827] [G loss: -1.709880]
195 [D loss: -36.964111] [G loss: -1.727154]
196 [D loss: -36.942955] [G loss: -1.739287]
197 [D loss: -36.925755] [G loss: -1.755899]
198 [D loss: -36.905128] [G loss: -1.758433]
199 [D loss: -36.890018] [G loss: -1.798711]
200 [D loss: -36.869892] [G loss: -1.813898]
201 [D loss: -36.851967] [G loss: -1.832991]
202 [D loss: -36.828445] [G loss: -1.844133]
203 [D loss: -36.806026] [G loss: -1.888153]
204 [D loss: -36.792645] [G loss: -1.909567]
205 [D loss: -36.770451] [G loss: -1.916096]
206 [D loss: -36.752022] [G loss: -1.926802]
207 [D loss: -36.725231] [G loss: -1.947262]
208 [D los

370 [D loss: -30.734167] [G loss: -7.612333]
371 [D loss: -30.674292] [G loss: -7.631499]
372 [D loss: -30.628487] [G loss: -7.712644]
373 [D loss: -30.565079] [G loss: -7.730747]
374 [D loss: -30.519428] [G loss: -7.807515]
375 [D loss: -30.448528] [G loss: -7.788705]
376 [D loss: -30.401226] [G loss: -7.883591]
377 [D loss: -30.344620] [G loss: -7.911385]
378 [D loss: -30.297670] [G loss: -7.979092]
379 [D loss: -30.225410] [G loss: -8.026214]
380 [D loss: -30.161842] [G loss: -8.119089]
381 [D loss: -30.110180] [G loss: -8.149186]
382 [D loss: -30.055199] [G loss: -8.245097]
383 [D loss: -30.004635] [G loss: -8.218856]
384 [D loss: -29.932846] [G loss: -8.323672]
385 [D loss: -29.869579] [G loss: -8.331870]
386 [D loss: -29.814226] [G loss: -8.448594]
387 [D loss: -29.761747] [G loss: -8.456549]
388 [D loss: -29.693672] [G loss: -8.544148]
389 [D loss: -29.644691] [G loss: -8.530858]
390 [D loss: -29.583490] [G loss: -8.640900]
391 [D loss: -29.512260] [G loss: -8.649170]
392 [D los

550 [D loss: -16.721891] [G loss: -19.585865]
551 [D loss: -16.628965] [G loss: -19.817291]
552 [D loss: -16.537758] [G loss: -19.734932]
553 [D loss: -16.429140] [G loss: -19.936525]
554 [D loss: -16.342937] [G loss: -19.872347]
555 [D loss: -16.226910] [G loss: -20.072584]
556 [D loss: -16.150572] [G loss: -19.988737]
557 [D loss: -16.054312] [G loss: -20.253260]
558 [D loss: -15.952553] [G loss: -20.211325]
559 [D loss: -15.848088] [G loss: -20.313343]
560 [D loss: -15.740767] [G loss: -20.559649]
561 [D loss: -15.674449] [G loss: -20.411135]
562 [D loss: -15.562802] [G loss: -20.613121]
563 [D loss: -15.457137] [G loss: -20.552797]
564 [D loss: -15.365705] [G loss: -20.844877]
565 [D loss: -15.286098] [G loss: -20.794096]
566 [D loss: -15.182512] [G loss: -20.810232]
567 [D loss: -15.087354] [G loss: -21.010771]
568 [D loss: -14.994680] [G loss: -20.902294]
569 [D loss: -14.888950] [G loss: -21.128988]
570 [D loss: -14.787254] [G loss: -21.054384]
571 [D loss: -14.693659] [G loss: 

...

99102 [D loss: -0.094716] [G loss: 2.177551]
99103 [D loss: -0.096392] [G loss: 2.138431]
99104 [D loss: -0.091039] [G loss: 2.125153]
99105 [D loss: -0.097088] [G loss: 2.210138]
99106 [D loss: -0.094587] [G loss: 2.118876]
99107 [D loss: -0.102102] [G loss: 2.222590]
99108 [D loss: -0.096632] [G loss: 2.146805]
99109 [D loss: -0.105599] [G loss: 2.172216]
99110 [D loss: -0.109102] [G loss: 2.082364]
99111 [D loss: -0.107703] [G loss: 2.188788]
99112 [D loss: -0.104757] [G loss: 2.113613]
99113 [D loss: -0.110251] [G loss: 2.167532]
99114 [D loss: -0.100588] [G loss: 2.062241]
99115 [D loss: -0.105871] [G loss: 2.193673]
99116 [D loss: -0.105420] [G loss: 2.057564]
99117 [D loss: -0.096344] [G loss: 2.128707]
99118 [D loss: -0.103761] [G loss: 2.133866]
99119 [D loss: -0.102534] [G loss: 2.026175]
99120 [D loss: -0.094706] [G loss: 2.065709]
99121 [D loss: -0.101090] [G loss: 2.098536]
99122 [D loss: -0.101189] [G loss: 2.120547]
99123 [D loss: -0.104073] [G loss: 2.138269]
99124 [D l

99286 [D loss: -0.092850] [G loss: 2.131027]
99287 [D loss: -0.089395] [G loss: 2.284588]
99288 [D loss: -0.097566] [G loss: 2.126458]
99289 [D loss: -0.102190] [G loss: 2.170173]
99290 [D loss: -0.097907] [G loss: 2.106544]
99291 [D loss: -0.107688] [G loss: 2.076180]
99292 [D loss: -0.103397] [G loss: 2.033441]
99293 [D loss: -0.100957] [G loss: 2.102441]
99294 [D loss: -0.100719] [G loss: 1.959332]
99295 [D loss: -0.098429] [G loss: 2.010820]
99296 [D loss: -0.097758] [G loss: 2.062599]
99297 [D loss: -0.093313] [G loss: 2.021134]
99298 [D loss: -0.095722] [G loss: 2.085557]
99299 [D loss: -0.092453] [G loss: 2.027907]
99300 [D loss: -0.090120] [G loss: 2.115766]
99301 [D loss: -0.100564] [G loss: 2.079959]
99302 [D loss: -0.092722] [G loss: 2.201981]
99303 [D loss: -0.084007] [G loss: 2.109815]
99304 [D loss: -0.087054] [G loss: 2.163107]
99305 [D loss: -0.086602] [G loss: 2.114415]
99306 [D loss: -0.073736] [G loss: 2.127365]
99307 [D loss: -0.081259] [G loss: 2.243956]
99308 [D l

99470 [D loss: -0.104360] [G loss: 2.265781]
99471 [D loss: -0.099369] [G loss: 2.324523]
99472 [D loss: -0.095969] [G loss: 2.254205]
99473 [D loss: -0.107570] [G loss: 2.276878]
99474 [D loss: -0.100998] [G loss: 2.275163]
99475 [D loss: -0.107805] [G loss: 2.219140]
99476 [D loss: -0.109469] [G loss: 2.272182]
99477 [D loss: -0.109198] [G loss: 2.225991]
99478 [D loss: -0.110174] [G loss: 2.292198]
99479 [D loss: -0.092619] [G loss: 2.322253]
99480 [D loss: -0.099039] [G loss: 2.323433]
99481 [D loss: -0.087883] [G loss: 2.331091]
99482 [D loss: -0.089241] [G loss: 2.370304]
99483 [D loss: -0.087325] [G loss: 2.375097]
99484 [D loss: -0.087966] [G loss: 2.387732]
99485 [D loss: -0.092111] [G loss: 2.408333]
99486 [D loss: -0.090480] [G loss: 2.435315]
99487 [D loss: -0.093215] [G loss: 2.415262]
99488 [D loss: -0.096483] [G loss: 2.462597]
99489 [D loss: -0.096337] [G loss: 2.438833]
99490 [D loss: -0.100612] [G loss: 2.496716]
99491 [D loss: -0.102355] [G loss: 2.472913]
99492 [D l

99654 [D loss: -0.101602] [G loss: 2.662669]
99655 [D loss: -0.111612] [G loss: 2.750138]
99656 [D loss: -0.107649] [G loss: 2.625341]
99657 [D loss: -0.109504] [G loss: 2.719933]
99658 [D loss: -0.113108] [G loss: 2.712366]
99659 [D loss: -0.120069] [G loss: 2.659076]
99660 [D loss: -0.118672] [G loss: 2.656930]
99661 [D loss: -0.115142] [G loss: 2.691639]
99662 [D loss: -0.118068] [G loss: 2.715061]
99663 [D loss: -0.111157] [G loss: 2.613762]
99664 [D loss: -0.115301] [G loss: 2.684672]
99665 [D loss: -0.109576] [G loss: 2.627004]
99666 [D loss: -0.116602] [G loss: 2.650117]
99667 [D loss: -0.113194] [G loss: 2.682350]
99668 [D loss: -0.112980] [G loss: 2.724198]
99669 [D loss: -0.109544] [G loss: 2.617406]
99670 [D loss: -0.112599] [G loss: 2.676044]
99671 [D loss: -0.121671] [G loss: 2.669088]
99672 [D loss: -0.114930] [G loss: 2.725834]
99673 [D loss: -0.121342] [G loss: 2.735415]
99674 [D loss: -0.113484] [G loss: 2.638062]
99675 [D loss: -0.117325] [G loss: 2.752514]
99676 [D l

99838 [D loss: -0.116766] [G loss: 2.501844]
99839 [D loss: -0.116645] [G loss: 2.504761]
99840 [D loss: -0.109023] [G loss: 2.584306]
99841 [D loss: -0.100511] [G loss: 2.531965]
99842 [D loss: -0.102843] [G loss: 2.602777]
99843 [D loss: -0.099979] [G loss: 2.587963]
99844 [D loss: -0.099247] [G loss: 2.621403]
99845 [D loss: -0.097735] [G loss: 2.684582]
99846 [D loss: -0.102280] [G loss: 2.669808]
99847 [D loss: -0.096926] [G loss: 2.688673]
99848 [D loss: -0.112979] [G loss: 2.766008]
99849 [D loss: -0.107824] [G loss: 2.734380]
99850 [D loss: -0.118775] [G loss: 2.762771]
99851 [D loss: -0.112208] [G loss: 2.675977]
99852 [D loss: -0.122891] [G loss: 2.724299]
99853 [D loss: -0.120644] [G loss: 2.721539]
99854 [D loss: -0.117427] [G loss: 2.708127]
99855 [D loss: -0.115690] [G loss: 2.709096]
99856 [D loss: -0.100413] [G loss: 2.719757]
99857 [D loss: -0.113396] [G loss: 2.730768]
99858 [D loss: -0.110062] [G loss: 2.642818]
99859 [D loss: -0.116248] [G loss: 2.763921]
99860 [D l

# 5. Saving the result matrix

In [27]:
outX = model.transform(X)
np.savetxt('outX500001_2,noise001,layer3.txt',outX)


In [6]:
outX = np.loadtxt('outX500001_2,noise001,layer3.txt')


# 6. Generating Trajectories from Numpy array

In [7]:
traj = md.load('traj_pbc.gro')

In [8]:
outX_reshape = outX.reshape(-1,24,3)


In [9]:
real_data_reshape = real_data.reshape(-1,24,3)


In [10]:
traj_outX = md.Trajectory(xyz=outX_reshape,topology=traj.top,time = np.arange(real_data_reshape.shape[0]))


In [16]:
traj_outX[:1000].save_gro(filename='GAN_generated_trajectory.gro')

In [12]:
traj_real = md.Trajectory(xyz=real_data_reshape,topology=traj.top,time = np.arange(real_data_reshape.shape[0]))


In [15]:
traj_real[:1000].save_gro(filename='real_trajectory.gro')

In [14]:
print(np.all(traj_outX.xyz == outX_reshape),np.all(traj_real.xyz == real_data_reshape))

True True


# 7. Calculating RMSD

In [ ]:
distances = np.empty((traj_outX.n_frames, traj_real.n_frames))
for i in range(traj_real.n_frames):
    distances[i] = md.rmsd(traj_real, traj_outX, i)
print('Max pairwise rmsd: %f nm' % np.max(distances))


# 8. Visualizing the resulting trajectories

In [25]:
view_real= nv.show_mdtraj(traj_real[:1000])
view_real.clear_representations()
view_real.add_point()
view_real.add_cartoon(color='blue')
view_real

NGLWidget(max_frame=999)

In [26]:
view_outX= nv.show_mdtraj(traj_outX[:1000])
view_outX.clear_representations()
view_outX.add_point()
view_outX.add_cartoon(color='blue')
view_outX

NGLWidget(max_frame=999)

# 9. Generating and saving the videos

In [32]:
download_folder = '/Users/berylxzhang/Desktop'
# moviepy_params = {  'codec': 'mpeg4'}
movie_real = MovieMaker(view_real, output='real_trajectoy.gif',download_folder=download_folder)
movie_real.make()

IntProgress(value=0, description='Rendering ...', max=999)

In [34]:
download_folder = '/Users/berylxzhang/Desktop'
# moviepy_params = {  'codec': 'mpeg4'}
movie_outX = MovieMaker(view_outX, output='Gan generated trajectory.avi', download_folder=download_folder)
movie_outX.make()

IntProgress(value=0, description='Rendering ...', max=999)